In [1]:
import pandas as pd
%matplotlib inline
import matplotlib
import matplotlib.pyplot as plt
import numpy as np
import os

In [47]:
#Reading users file:
u_cols = ['user_id', 'age', 'sex', 'occupation', 'zip_code']
# users = pd.read_csv('../matrix_factorization/data/ml-100k/includes_team_users.csv').drop("Unnamed: 0",axis=1)
users = pd.read_csv('../data/ml-latest-small/users')

#Reading ratings file:
r_cols = ['user_id', 'movie_id', 'rating', 'unix_timestamp']
ratings = pd.read_csv('../data/ml-20m/ratings.csv')
smaller_ratings = pd.read_csv('../data/ml-latest-small/ratings.csv')

#Reading items file:
# i_cols = ['movie id', 'movie title' ,'release date','video release date', 'IMDb URL', 'unknown', 'Action', 'Adventure',
# 'Animation', 'Children\'s', 'Comedy', 'Crime', 'Documentary', 'Drama', 'Fantasy',
# 'Film-Noir', 'Horror', 'Musical', 'Mystery', 'Romance', 'Sci-Fi', 'Thriller', 'War', 'Western']
# items = pd.read_csv('../matrix_factorization/data/ml-100k/u.item', sep='|', names=i_cols,
# encoding='latin-1')

items = pd.read_csv('../data/ml-20m/movies.csv')
smaller_items = pd.read_csv('../data/ml-latest-small/movies.csv')


In [5]:
ratings.head()


userId  movieId  rating   timestamp
0       1        2     3.5  1112486027
1       1       29     3.5  1112484676
2       1       32     3.5  1112484819
3       1       47     3.5  1112484727
4       1       50     3.5  1112484580

In [55]:
smaller_ratings.head()

userId  movieId  rating  timestamp
0       1        1     4.0  964982703
1       1        3     4.0  964981247
2       1        6     4.0  964982224
3       1       47     5.0  964983815
4       1       50     5.0  964982931

In [6]:
items.head()

movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  
0  Adventure|Animation|Children|Comedy|Fantasy  
1                   Adventure|Children|Fantasy  
2                               Comedy|Romance  
3                         Comedy|Drama|Romance  
4                                       Comedy

In [40]:
smaller_items.head()

movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  
0  Adventure|Animation|Children|Comedy|Fantasy  
1                   Adventure|Children|Fantasy  
2                               Comedy|Romance  
3                         Comedy|Drama|Romance  
4                                       Comedy

In [66]:
users = pd.DataFrame({"userId":ratings.userId.unique()})
print(len(users))
users.head()

138493


userId
0       1
1       2
2       3
3       4
4       5

In [69]:
users_smaller = pd.DataFrame({"userId":smaller_ratings.userId.unique()})
print(len(users_smaller))
users_smaller.head()

610


userId
0       1
1       2
2       3
3       4
4       5

In [8]:
genres =[]
for i,movie in enumerate(items.values):
    movie_genre = movie[2].split("|")
    for genre in movie_genre:
        if genre not in genres:
            genres.append(genre)

In [9]:
genres

['Adventure',
 'Animation',
 'Children',
 'Comedy',
 'Fantasy',
 'Romance',
 'Drama',
 'Action',
 'Crime',
 'Thriller',
 'Horror',
 'Mystery',
 'Sci-Fi',
 'IMAX',
 'Documentary',
 'War',
 'Musical',
 'Western',
 'Film-Noir',
 '(no genres listed)']

In [29]:
for genre in genres:
    items[genre] = 0

In [30]:
items.head()

movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  Adventure  Animation  \
0  Adventure|Animation|Children|Comedy|Fantasy          0          0   
1                   Adventure|Children|Fantasy          0          0   
2                               Comedy|Romance          0          0   
3                         Comedy|Drama|Romance          0          0   
4                                       Comedy          0          0   

   Children  Comedy  Fantasy  Romance  Drama  ...  Horror  Mystery  Sci-Fi  \
0         0       0        0        0      0  ...       0        0       0   
1         0       0        0        0      0  ...       0        0       0   
2         0       0        0        0      0  ...       0        0       0   
3         0       0        0        0      0  ...       0        0       0   
4         0       0        0        0      0  ...       0        0       0   

   IMAX  Documentary  War  Musical  Western  Film-Noir  (no genres listed)  
0     0            0    0        0        0          0                   0  
1     0            0    0        0        0          0                   0  
2     0            0    0        0        0          0                   0  
3     0            0    0        0        0          0                   0  
4     0            0    0        0        0          0                   0  

[5 rows x 23 columns]

In [35]:
def codeGenre(movie_id):
    genres = movie_id.genres.split("|")
    print(genres)
    for genre in genres:
        movie_id[genre] = 1
        

In [31]:
items.head()


movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  Adventure  Animation  \
0  Adventure|Animation|Children|Comedy|Fantasy          0          0   
1                   Adventure|Children|Fantasy          0          0   
2                               Comedy|Romance          0          0   
3                         Comedy|Drama|Romance          0          0   
4                                       Comedy          0          0   

   Children  Comedy  Fantasy  Romance  Drama  ...  Horror  Mystery  Sci-Fi  \
0         0       0        0        0      0  ...       0        0       0   
1         0       0        0        0      0  ...       0        0       0   
2         0       0        0        0      0  ...       0        0       0   
3         0       0        0        0      0  ...       0        0       0   
4         0       0        0        0      0  ...       0        0       0   

   IMAX  Documentary  War  Musical  Western  Film-Noir  (no genres listed)  
0     0            0    0        0        0          0                   0  
1     0            0    0        0        0          0                   0  
2     0            0    0        0        0          0                   0  
3     0            0    0        0        0          0                   0  
4     0            0    0        0        0          0                   0  

[5 rows x 23 columns]

In [42]:
genres = pd.get_dummies(items.genres.str.split('|',expand=True).stack()).sum(level=0)
genres.head()

(no genres listed)  Action  Adventure  Animation  Children  Comedy  Crime  \
0                   0       0          1          1         1       1      0   
1                   0       0          1          0         1       0      0   
2                   0       0          0          0         0       1      0   
3                   0       0          0          0         0       1      0   
4                   0       0          0          0         0       1      0   

   Documentary  Drama  Fantasy  Film-Noir  Horror  IMAX  Musical  Mystery  \
0            0      0        1          0       0     0        0        0   
1            0      0        1          0       0     0        0        0   
2            0      0        0          0       0     0        0        0   
3            0      1        0          0       0     0        0        0   
4            0      0        0          0       0     0        0        0   

   Romance  Sci-Fi  Thriller  War  Western  
0        0       0         0    0        0  
1        0       0         0    0        0  
2        1       0         0    0        0  
3        1       0         0    0        0  
4        0       0         0    0        0

In [45]:
items_new = pd.concat([items,genres], axis=1)

In [54]:
items_new.drop(labels="genres",axis=1)

movieId                                              title  \
0            1                                   Toy Story (1995)   
1            2                                     Jumanji (1995)   
2            3                            Grumpier Old Men (1995)   
3            4                           Waiting to Exhale (1995)   
4            5                 Father of the Bride Part II (1995)   
5            6                                        Heat (1995)   
6            7                                     Sabrina (1995)   
7            8                                Tom and Huck (1995)   
8            9                                Sudden Death (1995)   
9           10                                   GoldenEye (1995)   
10          11                     American President, The (1995)   
11          12                 Dracula: Dead and Loving It (1995)   
12          13                                       Balto (1995)   
13          14                                       Nixon (1995)   
14          15                            Cutthroat Island (1995)   
15          16                                      Casino (1995)   
16          17                       Sense and Sensibility (1995)   
17          18                                  Four Rooms (1995)   
18          19              Ace Ventura: When Nature Calls (1995)   
19          20                                 Money Train (1995)   
20          21                                  Get Shorty (1995)   
21          22                                     Copycat (1995)   
22          23                                   Assassins (1995)   
23          24                                      Powder (1995)   
24          25                           Leaving Las Vegas (1995)   
25          26                                     Othello (1995)   
26          27                                Now and Then (1995)   
27          28                                  Persuasion (1995)   
28          29  City of Lost Children, The (Cité des enfants p...   
29          30  Shanghai Triad (Yao a yao yao dao waipo qiao) ...   
...        ...                                                ...   
27248   131146                      Werner - Volles Rooäää (1999)   
27249   131148                                  What A Man (2011)   
27250   131150         7 Dwarves: The Forest Is Not Enough (2006)   
27251   131152                                 The Fat Spy (1966)   
27252   131154  Die Bademeister – Weiber, saufen, Leben retten...   
27253   131156                         Ants in the Pants 2 (2002)   
27254   131158                                Manta, Manta (1991)   
27255   131160                  Oscar and the Lady in Pink (2009)   
27256   131162                      Por un puñado de besos (2014)   
27257   131164                               Vietnam in HD (2011)   
27258   131166                                  WWII IN HD (2009)   
27259   131168                                     Phoenix (2014)   
27260   131170                                   Parallels (2015)   
27261   131172                              Closed Curtain (2013)   
27262   131174                                   Gentlemen (2014)   
27263   131176                             A Second Chance (2014)   
27264   131180                     Dead Rising: Watchtower (2015)   
27265   131231                                     Standby (2014)   
27266   131237                         What Men Talk About (2010)   
27267   131239                          Three Quarter Moon (2011)   
27268   131241                           Ants in the Pants (2000)   
27269   131243                Werner - Gekotzt wird später (2003)   
27270   131248                              Brother Bear 2 (2006)   
27271   131250                              No More School (2000)   
27272   131252  Forklift Driver Klaus: The First Day on the Jo...   
27273   131254                       Kein Bund für's Leben (2007)   
27274

In [88]:
print(smaller_ratings.shape)

(100836, 4)


In [93]:
print(items_new.shape)

(27278, 23)


In [94]:
n_users = smaller_ratings.userId.unique().shape[0]
n_items = smaller_ratings.movieId.unique().shape[0]

In [95]:
n_users

610

In [96]:
n_items

9724

In [98]:
data_matrix = np.zeros((n_users, n_items))
for line in smaller_ratings.itertuples():
    data_matrix[line[1]-1, line[2]-1] = line[3]

IndexError: index 46969 is out of bounds for axis 1 with size 9724

In [100]:
for line in smaller_ratings.itertuples():
    print(line)

Pandas(Index=0, userId=1, movieId=1, rating=4.0, timestamp=964982703)
Pandas(Index=1, userId=1, movieId=3, rating=4.0, timestamp=964981247)
Pandas(Index=2, userId=1, movieId=6, rating=4.0, timestamp=964982224)
Pandas(Index=3, userId=1, movieId=47, rating=5.0, timestamp=964983815)
Pandas(Index=4, userId=1, movieId=50, rating=5.0, timestamp=964982931)
Pandas(Index=5, userId=1, movieId=70, rating=3.0, timestamp=964982400)
Pandas(Index=6, userId=1, movieId=101, rating=5.0, timestamp=964980868)
Pandas(Index=7, userId=1, movieId=110, rating=4.0, timestamp=964982176)
Pandas(Index=8, userId=1, movieId=151, rating=5.0, timestamp=964984041)
Pandas(Index=9, userId=1, movieId=157, rating=5.0, timestamp=964984100)
Pandas(Index=10, userId=1, movieId=163, rating=5.0, timestamp=964983650)
Pandas(Index=11, userId=1, movieId=216, rating=5.0, timestamp=964981208)
Pandas(Index=12, userId=1, movieId=223, rating=3.0, timestamp=964980985)
Pandas(Index=13, userId=1, movieId=231, rating=5.0, timestamp=96498117

Pandas(Index=2408, userId=19, movieId=671, rating=2.0, timestamp=965703674)
Pandas(Index=2409, userId=19, movieId=673, rating=1.0, timestamp=965704355)
Pandas(Index=2410, userId=19, movieId=674, rating=4.0, timestamp=965703973)
Pandas(Index=2411, userId=19, movieId=708, rating=3.0, timestamp=965706615)
Pandas(Index=2412, userId=19, movieId=709, rating=2.0, timestamp=965709172)
Pandas(Index=2413, userId=19, movieId=711, rating=3.0, timestamp=965709923)
Pandas(Index=2414, userId=19, movieId=719, rating=2.0, timestamp=965707724)
Pandas(Index=2415, userId=19, movieId=720, rating=4.0, timestamp=965708982)
Pandas(Index=2416, userId=19, movieId=724, rating=4.0, timestamp=965705076)
Pandas(Index=2417, userId=19, movieId=733, rating=3.0, timestamp=965709534)
Pandas(Index=2418, userId=19, movieId=736, rating=2.0, timestamp=965709785)
Pandas(Index=2419, userId=19, movieId=742, rating=3.0, timestamp=965711994)
Pandas(Index=2420, userId=19, movieId=743, rating=2.0, timestamp=965707137)
Pandas(Index

Pandas(Index=4376, userId=28, movieId=2951, rating=3.0, timestamp=1234515633)
Pandas(Index=4377, userId=28, movieId=2952, rating=2.5, timestamp=1242106555)
Pandas(Index=4378, userId=28, movieId=2959, rating=3.5, timestamp=1234338005)
Pandas(Index=4379, userId=28, movieId=2968, rating=4.0, timestamp=1234334945)
Pandas(Index=4380, userId=28, movieId=2985, rating=3.0, timestamp=1277002126)
Pandas(Index=4381, userId=28, movieId=2997, rating=2.5, timestamp=1243837492)
Pandas(Index=4382, userId=28, movieId=3006, rating=2.5, timestamp=1234334969)
Pandas(Index=4383, userId=28, movieId=3020, rating=3.0, timestamp=1242032934)
Pandas(Index=4384, userId=28, movieId=3033, rating=3.0, timestamp=1277002147)
Pandas(Index=4385, userId=28, movieId=3052, rating=3.0, timestamp=1242290417)
Pandas(Index=4386, userId=28, movieId=3100, rating=4.0, timestamp=1242032411)
Pandas(Index=4387, userId=28, movieId=3105, rating=2.5, timestamp=1242031396)
Pandas(Index=4388, userId=28, movieId=3107, rating=2.0, timestam

Pandas(Index=6757, userId=45, movieId=3243, rating=2.0, timestamp=950740254)
Pandas(Index=6758, userId=45, movieId=3247, rating=3.0, timestamp=950740361)
Pandas(Index=6759, userId=45, movieId=3248, rating=2.0, timestamp=950740361)
Pandas(Index=6760, userId=45, movieId=3249, rating=3.0, timestamp=950740266)
Pandas(Index=6761, userId=45, movieId=3253, rating=4.0, timestamp=950740394)
Pandas(Index=6762, userId=45, movieId=3254, rating=4.0, timestamp=950740394)
Pandas(Index=6763, userId=45, movieId=3255, rating=3.0, timestamp=950740281)
Pandas(Index=6764, userId=45, movieId=3258, rating=3.0, timestamp=950740239)
Pandas(Index=6765, userId=45, movieId=3268, rating=1.0, timestamp=950740376)
Pandas(Index=6766, userId=45, movieId=3269, rating=3.0, timestamp=950741248)
Pandas(Index=6767, userId=45, movieId=3270, rating=1.0, timestamp=950718581)
Pandas(Index=6768, userId=45, movieId=3273, rating=4.0, timestamp=1007995150)
Pandas(Index=6769, userId=45, movieId=3274, rating=3.0, timestamp=950740361

Pandas(Index=9564, userId=64, movieId=1265, rating=4.0, timestamp=1161520350)
Pandas(Index=9565, userId=64, movieId=1266, rating=3.5, timestamp=1161528922)
Pandas(Index=9566, userId=64, movieId=1276, rating=4.0, timestamp=1161559678)
Pandas(Index=9567, userId=64, movieId=1282, rating=3.5, timestamp=1161559559)
Pandas(Index=9568, userId=64, movieId=1285, rating=3.0, timestamp=1161559782)
Pandas(Index=9569, userId=64, movieId=1287, rating=4.5, timestamp=1161566123)
Pandas(Index=9570, userId=64, movieId=1288, rating=4.5, timestamp=1161519737)
Pandas(Index=9571, userId=64, movieId=1293, rating=5.0, timestamp=1161564479)
Pandas(Index=9572, userId=64, movieId=1302, rating=4.0, timestamp=1161529469)
Pandas(Index=9573, userId=64, movieId=1320, rating=3.0, timestamp=1161528929)
Pandas(Index=9574, userId=64, movieId=1339, rating=3.5, timestamp=1161565604)
Pandas(Index=9575, userId=64, movieId=1343, rating=4.0, timestamp=1161564509)
Pandas(Index=9576, userId=64, movieId=1345, rating=4.5, timestam

...

Pandas(Index=80345, userId=507, movieId=589, rating=3.0, timestamp=838964703)
Pandas(Index=80346, userId=507, movieId=590, rating=3.0, timestamp=838964549)
Pandas(Index=80347, userId=507, movieId=593, rating=3.0, timestamp=838964592)
Pandas(Index=80348, userId=507, movieId=595, rating=3.0, timestamp=838964592)
Pandas(Index=80349, userId=508, movieId=107, rating=2.0, timestamp=1268297485)
Pandas(Index=80350, userId=508, movieId=135, rating=1.0, timestamp=1268297488)
Pandas(Index=80351, userId=508, movieId=307, rating=1.0, timestamp=1268297492)
Pandas(Index=80352, userId=508, movieId=562, rating=2.5, timestamp=1268297537)
Pandas(Index=80353, userId=508, movieId=671, rating=2.5, timestamp=1268297502)
Pandas(Index=80354, userId=508, movieId=799, rating=2.0, timestamp=1268297532)
Pandas(Index=80355, userId=508, movieId=898, rating=2.0, timestamp=1268297515)
Pandas(Index=80356, userId=508, movieId=1175, rating=1.5, timestamp=1268297518)
Pandas(Index=80357, userId=508, movieId=1222, rating=4.

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




Pandas(Index=93782, userId=599, movieId=4008, rating=3.5, timestamp=1498797606)
Pandas(Index=93783, userId=599, movieId=4010, rating=2.0, timestamp=1519180481)
Pandas(Index=93784, userId=599, movieId=4011, rating=3.0, timestamp=1498519789)
Pandas(Index=93785, userId=599, movieId=4012, rating=2.0, timestamp=1498510275)
Pandas(Index=93786, userId=599, movieId=4014, rating=2.5, timestamp=1498518686)
Pandas(Index=93787, userId=599, movieId=4015, rating=2.0, timestamp=1498510508)
Pandas(Index=93788, userId=599, movieId=4017, rating=2.5, timestamp=1498518582)
Pandas(Index=93789, userId=599, movieId=4019, rating=2.0, timestamp=1519177641)
Pandas(Index=93790, userId=599, movieId=4022, rating=2.5, timestamp=1498516526)
Pandas(Index=93791, userId=599, movieId=4027, rating=3.5, timestamp=1498501454)
Pandas(Index=93792, userId=599, movieId=4029, rating=3.0, timestamp=1498524417)
Pandas(Index=93793, userId=599, movieId=4034, rating=2.0, timestamp=1498511276)
Pandas(Index=93794, userId=599, movieId

Pandas(Index=96677, userId=603, movieId=2529, rating=4.0, timestamp=963177215)
Pandas(Index=96678, userId=603, movieId=2530, rating=4.0, timestamp=963177159)
Pandas(Index=96679, userId=603, movieId=2531, rating=4.0, timestamp=963177159)
Pandas(Index=96680, userId=603, movieId=2532, rating=4.0, timestamp=963177144)
Pandas(Index=96681, userId=603, movieId=2533, rating=4.0, timestamp=953927060)
Pandas(Index=96682, userId=603, movieId=2539, rating=4.0, timestamp=963178528)
Pandas(Index=96683, userId=603, movieId=2540, rating=3.0, timestamp=963177719)
Pandas(Index=96684, userId=603, movieId=2544, rating=3.0, timestamp=963179791)
Pandas(Index=96685, userId=603, movieId=2551, rating=5.0, timestamp=953927884)
Pandas(Index=96686, userId=603, movieId=2558, rating=1.0, timestamp=963178960)
Pandas(Index=96687, userId=603, movieId=2567, rating=2.0, timestamp=963178568)
Pandas(Index=96688, userId=603, movieId=2570, rating=3.0, timestamp=954482443)
Pandas(Index=96689, userId=603, movieId=2571, rating

Pandas(Index=98969, userId=608, movieId=1882, rating=1.5, timestamp=1117415532)
Pandas(Index=98970, userId=608, movieId=1907, rating=3.5, timestamp=1117504918)
Pandas(Index=98971, userId=608, movieId=1909, rating=3.5, timestamp=1117504548)
Pandas(Index=98972, userId=608, movieId=1911, rating=3.5, timestamp=1117504945)
Pandas(Index=98973, userId=608, movieId=1917, rating=3.5, timestamp=1117504416)
Pandas(Index=98974, userId=608, movieId=1918, rating=3.0, timestamp=1117504702)
Pandas(Index=98975, userId=608, movieId=1921, rating=4.5, timestamp=1117336833)
Pandas(Index=98976, userId=608, movieId=1923, rating=3.5, timestamp=1117408287)
Pandas(Index=98977, userId=608, movieId=1953, rating=4.5, timestamp=1117504693)
Pandas(Index=98978, userId=608, movieId=1954, rating=4.5, timestamp=1117504516)
Pandas(Index=98979, userId=608, movieId=1961, rating=4.5, timestamp=1117409451)
Pandas(Index=98980, userId=608, movieId=1968, rating=4.0, timestamp=1117415321)
Pandas(Index=98981, userId=608, movieId=